# Disaster ORS: Avoid Feature Example

In [1]:
#from IPython.display import *
#from IPython.display import HTML, display

import folium
from folium import Map, Marker, FeatureGroup, LayerControl
from folium.plugins import MarkerCluster

from openrouteservice import client

import fiona as fn
from shapely.geometry import shape, Polygon, mapping, MultiPolygon
from shapely.ops import cascaded_union, unary_union

from pprint import pprint

## Preprocessing

Three different data sets were received from [Landesbetrieb für Hochwasserschutz und Wasserwirtschaft Sachsen-Anhalt](http://www.geofachdatenserver.de/de/lhw-hochwassergefahrenkarten.html) (07.08.2018). Data 'HQ10' with a high flood risk, data 'HQ100' with a medium flood risk and data 'HQ200' with a low flood risk, but which represents a extrem event. 

Each data set were given as single files (each file represents one quarter of the area), therefore it were merged in QGIS to one file per risk scenario.  

In [16]:
# insert your ORS api key
api_key = 'YOUR-KEY' 
clnt = client.Client(key=api_key)

# Maps with different flood risk
map_HQ10 = folium.Map(tiles='Stamen Toner', location=([52.126849, 11.643448]), zoom_start=10)
map_HQ100 = folium.Map(tiles='Stamen Toner', location=([52.126849, 11.643448]), zoom_start=10)
map_HQ200 = folium.Map(tiles='Stamen Toner', location=([52.126849, 11.643448]), zoom_start=10)

def style_function(color): # To style data
    return lambda feature: dict(color=color)

# Data Dictionary
data_dict = {
    'HQ200/HQ200_clip.shp': {'style': '#1ac6ff',  # HQ200: low possibility, extrem event
                            'group': FeatureGroup(name='HQ200'),
                            'map': map_HQ200},
    'HQ100/HQ100_clip.shp': {'style': '#3366ff',  # HQ100: medium possibility
                             'group': FeatureGroup(name='HQ100'),
                            'map': map_HQ100},
    'HQ10/HQ10_clip.shp': {'style': '#000099',  # HQ10: high possibility
                           'group': FeatureGroup(name='HQ10'),
                            'map': map_HQ10}
}


# Visualize Data
HQ_multipoly = [] # Create one list with all data sets
for geojson in range(len(data_dict)):
    HQ_multipoly.append([])
    for file in data_dict:
        with fn.open(file, 'r') as HQ_x:
            for data in HQ_x:
                # Simplify data for better handling
                geom = shape(data['geometry'])
                simp_geom = geom.simplify(0.0005, preserve_topology=False)
                HQ_x_coord = mapping(simp_geom)
                HQ_multipoly[geojson].append(simp_geom)
                folium.features.GeoJson(data=HQ_x_coord,
                                        name=file,
                                        style_function=style_function(data_dict[file]['style'])).add_to(data_dict[file]['group'])
        data_dict[file]['group'].add_to(data_dict[file]['map'])

## Generating maps

In [ ]:
# generate routes considering and not considering the flood affected areas 
#(just as a very easy showcase to proof that the areas are avoided)

Routing with OpenRouteService is easily done and full of options. One Option is to avoid areas and given polygons. In this the flooded areas are supposed to avoid. Because the `avoid_polygons` paramater can just take geojsons with a maximum number of coordinates, the data has to be simplified. A concave hull were generated in QGIS. 

Two routes for each scenario were generated. First the regular route and second a route which avoid the flooded areas. 

In [19]:
# Concave hull of polygons
contour_dict = {
    'HQ200/HQ200_contour.shp': {'map': map_HQ200},
    'HQ100/HQ100_contour.shp': {'map': map_HQ100},
    'HQ10/HQ10_contour1.shp': {'map': map_HQ10}
}

start = [11.56105, 52.129168]#[11.668425, 52.204083]#[11.520538, 52.149501] 
destination = [11.791935, 52.211288]#[11.686878, 52.214523]#[11.47728, 52.084992] #[11.686878, 52.214523]

# Routing parameters
request = {'coordinates': [start, destination], 
            'format_out': 'geojson',
            'profile': 'driving-car',
            'preference': 'shortest',
            'instructions': False}
normal_directions = clnt.directions(**request)

# Request and visualize data
HQ_contour = []
for geojson in range(len(contour_dict)):
    HQ_contour.append([])
    for file in contour_dict:
        with fn.open(file, 'r') as contour:
            for data in contour:
                geom = shape(data['geometry'])
                HQ_contour[geojson].append(geom)
                
                # Regular route
                folium.features.GeoJson(data=normal_directions,
                                        name='regular',
                                        style_function=style_function('purple')).add_to(contour_dict[file]['map'])
                                
                # Route in case of a flood 
                request['options'] =  {'avoid_polygons': mapping(geom)} 
                avoid_directions = clnt.directions(**request)
                folium.features.GeoJson(data=avoid_directions,
                            name='avoid',
                            style_function=style_function('red')).add_to(contour_dict[file]['map'])

In [20]:
# Map with high flood risk
map_HQ10.add_child(folium.map.LayerControl())
map_HQ10

In [21]:
# Map with medium flood risk
map_HQ100.add_child(folium.map.LayerControl())
map_HQ100

In [15]:
# Map with low flood risk; extrem event
map_HQ200.add_child(folium.map.LayerControl())
map_HQ200

In [ ]:
# decide for a second area of interest and use point information to derive the areas to avoid 
#(e.g. georeferenced points from social media which indicate blocked streets.)

In [ ]:
# apply a buffer to generate areas for the points and then calculate the routes # points = hospitals?